In [88]:
import pandas as pd
import geopandas as gpd
import shapely
from shapely.geometry import Polygon, Point, MultiPoint
import math
import matplotlib.pyplot as plt
import numpy as np
from numpy import exp
from numpy.random import rand, seed
import folium
import random 
import osmnx as ox
import networkx as nx
import warnings
from shapely.errors import ShapelyDeprecationWarning
warnings.simplefilter('ignore', ShapelyDeprecationWarning)
pd.options.mode.chained_assignment = None  # default='warn'

In [99]:
# read, process, and save data from 00_data_forModel_all excel sheet

# A10 boundary
a10 = gpd.read_file('data/A10.shp')
a10 = a10.to_crs('EPSG:4326')
a10.to_file('data/data_cleaned/a10.shp')

materialNames_conversion = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='materialNames_conversion')
materials_logistics_info = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='materials_logistics_info')
buildingTypes_matComposition = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='buildingTypes_matComposition')
vehicles_info = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='vehicles_info')
suppliers = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='suppliers')
hubs_macro = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='hubs_macro')
hubs_candidateLocations = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='hubs_candidateLocations')
construction_sites = pd.read_excel('data/00_data_forModel_all.xlsx', sheet_name='construction_sites')

locationData_dict = {
    'suppliers': suppliers,
    'hubs_macro': hubs_macro,
    'hubs_candidateLocations': hubs_candidateLocations,
    'construction_sites': construction_sites
}
nonLocationData_dict = {
    'materialNames_conversion': materialNames_conversion, 
    'materials_logistics_info': materials_logistics_info,
    'buildingType_info': buildingTypes_matComposition,
    'vehicles_info': vehicles_info, 
    'suppliers': suppliers
}

def df_to_gdf(df): 
    df['geometry'] = df.apply(lambda row: Point(row.lng, row.lat), axis=1)
    gdf = gpd.GeoDataFrame(df, geometry='geometry', crs='EPSG:4326').drop(columns=['lat', 'lng'])
    return gdf

for key in locationData_dict.keys(): 
    gdf = df_to_gdf(locationData_dict[key])
    locationData_dict[key] = gdf
    gdf.to_file(f'data/data_cleaned/{key}.shp')
    
for key, df in nonLocationData_dict.items(): 
    if key == 'buildingType_info': 
        df.rename(columns={'amount_mid-rise': 'A', 'amount_high-rise': 'B', 
                          'biobased_type': 'biobased_type', 
                           'structural_type': 'structural_type'}, inplace=True)
        df = df.melt(
            id_vars=['material', 'unit', 'biobased_type', 'structural_type'], 
            value_vars=['A', 'B'], 
            var_name='buildingType', 
            value_name='tons'
        )
    for col in df.columns: 
        if df[col].dtype == 'O': 
            df[col] = df[col].map(lambda x: x.strip())
    nonLocationData_dict[key] = df
    df.to_csv(f'data/data_cleaned/{key}.csv', index=False)
    
# add material capacity columns to vehicles_info
m = nonLocationData_dict['materials_logistics_info'].copy()
def make_capacity_columns(row): 
    for mat in m.material: 
        if mat == 'modules': 
            row[f'capacity_{mat}'] = 2
            continue
        mat_info = m[m.material == mat].iloc[0]
        if mat_info.main_unit == 'tons': 
            max_tons = row.max_tons
        elif mat_info.main_unit == 'm3': 
            max_m3 = row.max_m3
            max_tons = row.max_tons * mat_info.m3_to_t
        row[f'capacity_{mat}'] = round(max_tons * mat_info.perc_fill_total,1)
    return row 
nonLocationData_dict['vehicles_info'] = nonLocationData_dict['vehicles_info'].apply(lambda row: make_capacity_columns(row), axis=1)
nonLocationData_dict['vehicles_info'].to_csv(f'data/data_cleaned/vehicles_info.csv', index=False)
nonLocationData_dict['materials_logistics_info'].to_csv(f'data/data_cleaned/materials_logistics_info.csv', index=False)

# make and save hub gdf with both macro and micro hubs
sites_n = locationData_dict['construction_sites'].to_crs('EPSG:28992')
sites_n.geometry = sites_n.geometry.buffer(2000)
minx, miny, maxx, maxy = sites_n.to_crs('EPSG:4326').total_bounds
microHubs = locationData_dict['hubs_candidateLocations'].cx[minx:maxx, miny:maxy] 
microHubs['hub_type'] = 'micro'
macroHubs = hubs_macro.copy()
macroHubs = macroHubs[['name', 'hub_type', 'geometry']]
hubs = pd.concat([macroHubs, microHubs]).reset_index(drop=True)
hubs = hubs.reset_index(names='hub_id')
hubs = hubs[['hub_id', 'hub_type', 'geometry']]
hubs = gpd.GeoDataFrame(hubs)
hubs = hubs.to_crs('EPSG:28992')
macro = hubs[hubs.hub_type == 'macro']
hubs['nearMacro'] = macro.geometry.sindex.nearest(list(hubs.geometry))[1]
hubs['inA10'] = hubs.geometry.within(a10.geometry[0])
hubs = hubs.to_crs('EPSG:4326')
hubs.to_file('data/data_cleaned/hubs.shp')

# add building type
sites = locationData_dict['construction_sites'].copy()
buildingType_list = ['A', 'B']
sites['buildType'] = np.random.choice(buildingType_list, size=len(sites))
sites['inA10'] = sites.geometry.within(a10.geometry[0])
sites.to_file('data/data_cleaned/construction_sites.shp')

# make vehicles_info_demSites
vehicles_info = nonLocationData_dict['vehicles_info']
mat_conversion = nonLocationData_dict['materialNames_conversion']
mat_conversion = mat_conversion.groupby(by = 'name_from_demSiteData')['name_from_conSiteData'].agg(list).reset_index()
demSites_mat_list = ['steel', 'copper', 'aluminium', 'timber', 'concrete', 
                     'brick', 'glass', 'ceramic', 'plastic', 'insulation', 'other']

def make_demSite_capacities(row): 
    for mat in mat_conversion.name_from_demSiteData.unique():
        conSite_names = mat_conversion[mat_conversion.name_from_demSiteData == mat].iloc[0].name_from_conSiteData
        capacities = []
        for name in conSite_names: 
            temp = vehicles_info.copy()
            temp = temp[(temp.region == row.region) & 
                        (temp.transportation_network == row.transportation_network) & 
                        (temp.vehicle_type == row.vehicle_type)].iloc[0]
            capacity_con = temp[f'capacity_{name}']
            capacities.append(capacity_con)
        capacity = sum(capacities) / len(capacities)
        row[f'capacity_{mat}'] = capacity 
    return row 
    
vehicles_demSites = vehicles_info.copy() 
vehicles_demSites = vehicles_demSites.drop([col for col in vehicles_demSites if col.startswith('capacity')], axis=1)
vehicles_demSites = vehicles_demSites.apply(lambda row: make_demSite_capacities(row), axis=1)
vehicles_demSites.to_csv('data/data_cleaned/vehicles_info_demSites.csv')

In [100]:
%%time
# gdf of supply of secondary resources 
supplyFile = gpd.read_file('../_bigData/pblUrbanMiningModels/shpsCleaned/supply_NL.shp')
supplyFile = supplyFile.reset_index(drop=True)

xmin, ymin, xmax, ymax = sites.to_crs('EPSG:28992').total_bounds
buffer = 15000
xmin, ymin = xmin-buffer, ymin-buffer
xmax, ymax = xmax+buffer, ymax+buffer

supply = supplyFile.copy()
supply = supply.cx[xmin:xmax, ymin:ymax]

supply = supply[(supply.buildYear > 1920) & (supply.buildYear < 1980)]
supply = supply.sort_values('buildYear')
nRows = int(len(supply) / 1) # oldest 1/6 of cells  
supply = supply.head(nRows)
supply.buildYear = supply.buildYear.map(lambda x: int(math.floor(x)))
supply = supply[['buildYear', 'class', 
                 'steel', 'copper', 'aluminium', 'wood', 
                 'concrete', 'brick', 'glass','ceramic', 
                 'plastic', 'insulat', 'overig', 'geometry']]
for mat in ['steel', 'copper', 'aluminium', 'wood', 'concrete', 
            'brick', 'glass','ceramic', 'plastic', 'insulat', 'overig']: 
    supply[mat] = supply[mat].map(lambda x: x/1000)
supply.rename(columns={'wood': 'timber', 'insulat': 'insulation', 'overig': 'other'}, inplace=True)
demSites = supply.copy()
demSites = demSites.reset_index(drop=True).reset_index(names='id')
demSites = demSites.to_crs('EPSG:4326')
demSites_hires = demSites.copy()

# simplify demSites to grid of 1km by 1km rather than 100m by 100m 
def compute_grid_cell(point, size=1000):
    x, y = point.x, point.y
    x_min, x_max = x - (x % size), x - (x % size) + size
    y_min, y_max = y - (y % size), y - (y % size) + size
    return Polygon([(x_min, y_min), (x_min, y_max), (x_max, y_max), (x_max, y_min)])
demSites = demSites.to_crs('EPSG:28992')
demSites['grid_cell'] = demSites.geometry.apply(compute_grid_cell)
demSites = demSites.groupby('grid_cell', sort=False).sum(numeric_only=True).reset_index()
demSites = gpd.GeoDataFrame(demSites, geometry=demSites.grid_cell, crs='EPSG:28992')
demSites.geometry = demSites.geometry.centroid
demSites = demSites.to_crs('EPSG:4326')
demSites.drop(columns=['grid_cell', 'id', 'buildYear'], inplace=True)
demSites['inA10'] = demSites.geometry.within(a10.geometry[0])

CPU times: total: 5.08 s
Wall time: 5.19 s


In [101]:
# add ids exactly like the model 
sites['unique_id'] = pd.Series(range(len(sites)))
suppliers['unique_id'] = pd.Series(range(len(sites), 
                                         len(sites)+len(suppliers)))
hubs['unique_id'] = pd.Series(range(len(sites)+len(suppliers), 
                                    len(sites)+len(suppliers)+len(hubs)))
demSites['unique_id'] = pd.Series(range(len(sites)+len(suppliers)+len(hubs), 
                                        len(sites)+len(suppliers)+len(hubs)+len(demSites)))

In [102]:
%%time
def add_waterbound_column(water, gdf):
    gdf = gdf.to_crs('EPSG:28992')
    water = water.to_crs('EPSG:28992')
    gdf.geometry = gdf.geometry.buffer(100)
    
    sindex = water.sindex
    possible_matches_index = gdf.apply(lambda x: list(sindex.intersection(x.geometry.bounds)), axis=1)
    possible_matches = possible_matches_index.apply(lambda x: water.iloc[x])
    precise_matches = possible_matches.apply(lambda x: x.unary_union if x is not None else None)
    gdf['waterbound'] = gdf.apply(lambda x: x.geometry.intersects(precise_matches.loc[x.name]) if precise_matches.loc[x.name] is not None else False, axis=1)
    
    gdf.geometry = gdf.geometry.centroid
    gdf = gdf.to_crs('EPSG:4326')
    return gdf 

water = gpd.read_file('data/ams_water.gml')
water = water.set_crs('EPSG:28992')
water_all = water.unary_union

demSites = add_waterbound_column(water, demSites)
hubs = add_waterbound_column(water, hubs)
sites = add_waterbound_column(water, sites)

demSites.to_file('data/data_cleaned/demolition_sites.shp')
sites.to_file('data/data_cleaned/construction_sites.shp')
hubs.to_file('data/data_cleaned/hubs.shp')

CPU times: total: 2 s
Wall time: 2.07 s


In [149]:
m = folium.Map([52.377231, 4.899288], zoom_start=11, tiles='cartodbdark_matter')
# for _, row in demSites.iterrows(): 
#     folium.CircleMarker([row.geometry.y, row.geometry.x], 
#                         color='grey', radius=0.5).add_to(m)
for _, row in sites.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='white', radius=0.5).add_to(m)
for _, row in hubs.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='red', radius=0.5).add_to(m)
# for _, row in microHubs_n.iterrows(): 
#     folium.CircleMarker([row.geometry.y, row.geometry.x], 
#                         color='red', radius=0.5).add_to(m)
m

# street network

In [103]:
%%time

# make bounding box for MRA 
xmin, ymin, xmax, ymax = demSites.to_crs('EPSG:28992').total_bounds
bbox = Polygon([(xmin, ymin), (xmin, ymax), (xmax, ymax), (xmax, ymin)]).buffer(1000)
gdf = gpd.GeoDataFrame({'geometry': [bbox]}, crs="EPSG:28992")
xmin, ymin, xmax, ymax = gdf.to_crs('EPSG:4326').total_bounds

# fetch osmnx graph road network for MRA
custom_filter = '["highway"~"motorway|trunk|primary|secondary|tertiary"]'
G = ox.graph_from_bbox(ymax, ymin, xmax, xmin, network_type='drive', 
                          custom_filter=custom_filter) 
G = ox.utils_graph.get_largest_component(G, strongly=False)
G = G.to_undirected()

# fix speed limits 
default_speed = 50
for u, v, key, data in G.edges(keys=True, data=True):
    if 'maxspeed' not in data:
        data['maxspeed'] = default_speed
    elif isinstance(data['maxspeed'], list):
        data['maxspeed'] = [int(s) for s in data['maxspeed']]
        data['maxspeed'] = int(sum(data['maxspeed']) / len(data['maxspeed']))
    else: 
        data['maxspeed'] = int(data['maxspeed'])
        
# Add travel time (in minutes) for all edges
for u, v, key, data in G.edges(keys=True, data=True):
    data['time'] = data['length'] / (data['maxspeed'] * 1000) * 60

CPU times: total: 22.2 s
Wall time: 22.9 s


In [104]:
sites = gpd.read_file('data/data_cleaned/construction_sites.shp')
suppliers = gpd.read_file('data/data_cleaned/suppliers.shp')
hubs = gpd.read_file('data/data_cleaned/hubs.shp')
demSites = gpd.read_file('data/data_cleaned/demolition_sites.shp')

seconds_perPath = 0.25
nPts = {'sites':len(sites), 'suppliers':len(suppliers), 'hubs':len(hubs), 
        'demSites':len(demSites), 'macroHubs':2}
pairs = [['hubs', 'sites'], ['macroHubs', 'hubs'], ['demSites', 'macroHubs'], 
        ['suppliers', 'macroHubs'], ['suppliers', 'sites']]
nPaths = 0
for pair in pairs:
    nPaths += nPts[pair[0]] * nPts[pair[1]]

print(f'estimated time for od matrix: {nPaths * seconds_perPath / 60} minutes')

estimated time for od matrix: 6.666666666666667 minutes


In [105]:
%%time 
# make unique_ids for gdfs of sites, suppliers, and hubs
# read files exactly the same way as model
sites = gpd.read_file('data/data_cleaned/construction_sites.shp')
suppliers = gpd.read_file('data/data_cleaned/suppliers.shp')
hubs = gpd.read_file('data/data_cleaned/hubs.shp')
demSites = gpd.read_file('data/data_cleaned/demolition_sites.shp')

# add ids exactly like the model 
sites['unique_id'] = pd.Series(range(len(sites)))
suppliers['unique_id'] = pd.Series(range(len(sites), 
                                         len(sites)+len(suppliers)))
hubs['unique_id'] = pd.Series(range(len(sites)+len(suppliers), 
                                    len(sites)+len(suppliers)+len(hubs)))
demSites['unique_id'] = pd.Series(range(len(sites)+len(suppliers)+len(hubs), 
                                        len(sites)+len(suppliers)+len(hubs)+len(demSites)))

def make_od_matrix(G, gdf_ori, gdf_dest): 
    od_matrix = []
    for _, ori_row in gdf_ori.iterrows():
        ori_point = ori_row.geometry
        ori_node = ox.distance.nearest_nodes(G, ori_point.x, ori_point.y)
        for _, dest_row in gdf_dest.iterrows():
            dest_point = dest_row.geometry
            dest_node = ox.distance.nearest_nodes(G, dest_point.x, dest_point.y)
            shortest_path = nx.shortest_path(G, ori_node, dest_node, weight='time', method='dijkstra')
            distance = sum(G[shortest_path[i]][shortest_path[i + 1]][0]['length'] for i in range(len(shortest_path) - 1))
            od_matrix.append([ori_row.unique_id, dest_row.unique_id, round(distance/1000, 3)])
    return np.array(od_matrix)

def make_edgeIds_matrix(G, gdf_ori, gdf_dest): 
    edgeIds_matrix = []
    for _, ori_row in gdf_ori.iterrows():
        ori_point = ori_row.geometry
        ori_node = ox.distance.nearest_nodes(G, ori_point.x, ori_point.y)
        for _, dest_row in gdf_dest.iterrows():
            dest_point = dest_row.geometry
            dest_node = ox.distance.nearest_nodes(G, dest_point.x, dest_point.y)
            shortest_path = nx.shortest_path(G, ori_node, dest_node, weight='time', method='dijkstra')
            road_segments = [(shortest_path[i], shortest_path[i+1]) for i in range(len(shortest_path)-1)]
            edge_ids = [G[u][v][0]['osmid'] for u, v in road_segments]
            edge_ids = [','.join(map(str, e)) if isinstance(e, list) else str(e) for e in edge_ids]
            edgeIds_matrix.append([ori_row.unique_id, dest_row.unique_id, edge_ids])
    return np.array(edgeIds_matrix, dtype=object)

macroHubs = hubs[hubs.hub_type == 'macro']

print('making od matrix for h2c, h2h... ')
od_matrix_h2c = make_od_matrix(G, hubs, sites)
od_matrix_h2h = make_od_matrix(G, macroHubs, hubs)
od_matrix_h2hc = np.vstack((od_matrix_h2c, od_matrix_h2h))
print('making od matrix for d2h, s2h, s2c...')
od_matrix_d2h = make_od_matrix(G, demSites, macroHubs)
od_matrix_s2h = make_od_matrix(G, suppliers, macroHubs)
od_matrix_s2c = make_od_matrix(G, suppliers, sites)

print('making edgeIds matrix for h2c, h2h... ')
edgeIds_matrix_h2c = make_edgeIds_matrix(G, hubs, sites)
edgeIds_matrix_h2h = make_edgeIds_matrix(G, macroHubs, hubs)
edgeIds_matrix_h2hc = np.vstack((edgeIds_matrix_h2c, edgeIds_matrix_h2h))
print('making edgeIds matrix for d2h, s2h, s2c... ')
edgeIds_matrix_d2h = make_edgeIds_matrix(G, demSites, macroHubs)
edgeIds_matrix_s2h = make_edgeIds_matrix(G, suppliers, macroHubs)
edgeIds_matrix_s2c = make_edgeIds_matrix(G, suppliers, sites)

making od matrix for h2c, h2h... 
making od matrix for d2h, s2h, s2c...
making edgeIds matrix for h2c, h2h... 
making edgeIds matrix for d2h, s2h, s2c... 
CPU times: total: 3min 51s
Wall time: 3min 54s


In [106]:
%%time
# make nodes, edges gdf from graph G
nodes, edges = ox.graph_to_gdfs(G)

# select edges within edgeIds_matrix_all 
edges.osmid = edges.osmid.map(lambda x: ','.join(map(str,x)) if isinstance(x, list) else str(x))
edges = edges[['osmid', 'geometry']]
edges = edges.reset_index(drop=True)
edges['nTrips'] = 0
edgeIds_matrix_all = np.vstack((edgeIds_matrix_s2h, edgeIds_matrix_d2h, edgeIds_matrix_h2hc))
osmidList = [item for sublist in edgeIds_matrix_all[:, 2] for item in sublist]
osmidList = [','.join(map(str, item)) if isinstance(item, list) else str(item) for item in osmidList]
edges = edges[edges['osmid'].isin(osmidList)]

CPU times: total: 2.62 s
Wall time: 2.71 s


In [107]:
ori_id = 21
dest_id = 23
roadMatrix = edgeIds_matrix_s2h

roadIds = roadMatrix[(roadMatrix[:, 0] == ori_id) & 
                     (roadMatrix[:, 1] == dest_id)][0][2]
path = edges[edges.osmid.isin(roadIds)]
supplier = suppliers[suppliers.unique_id == ori_id]
hub = hubs[hubs.unique_id == dest_id]

m = folium.Map([52.377231, 4.899288], zoom_start=11, tiles='cartodbdark_matter')
for _, row in hub.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='white', radius=3).add_to(m)
for _, row in supplier.iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='lightblue', radius=0.5).add_to(m)
for _, row in path.iterrows():
    folium.PolyLine([(lat, lon) for lat, lon in zip(row.geometry.xy[1], row.geometry.xy[0])],
                           color='red', weight=1.5).add_to(m)

m

In [108]:
%%time
# save gdfs to disk
ox.io.save_graphml(G, filepath="data/data_cleaned/ams_roads.graphml")
nodes.to_file('data/data_cleaned/ams_roads_nodes.shp')
edges.to_file('data/data_cleaned/ams_roads_edges.shp')

# save od matrices to disk 
np.save('data/data_cleaned/od_matrix_h2c.npy', od_matrix_h2c)
np.save('data/data_cleaned/od_matrix_h2h.npy', od_matrix_h2h)
np.save('data/data_cleaned/od_matrix_h2hc.npy', od_matrix_h2hc)
np.save('data/data_cleaned/od_matrix_d2h.npy', od_matrix_d2h)
np.save('data/data_cleaned/od_matrix_s2h.npy', od_matrix_s2h)
np.save('data/data_cleaned/od_matrix_s2c.npy', od_matrix_s2c)

# save od matrices to disk 
np.save('data/data_cleaned/roadOsmIds_matrix_h2c.npy', edgeIds_matrix_h2c)
np.save('data/data_cleaned/roadOsmIds_matrix_h2h.npy', edgeIds_matrix_h2h)
np.save('data/data_cleaned/roadOsmIds_matrix_h2hc.npy', edgeIds_matrix_h2hc)
np.save('data/data_cleaned/roadOsmIds_matrix_d2h.npy', edgeIds_matrix_d2h)
np.save('data/data_cleaned/roadOsmIds_matrix_s2h.npy', edgeIds_matrix_s2h)
np.save('data/data_cleaned/roadOsmIds_matrix_s2c.npy', edgeIds_matrix_s2c)

# save all shpfiles
suppliers.to_file('data/data_cleaned/suppliers.shp')
sites.to_file('data/data_cleaned/construction_sites.shp')
demSites.to_file('data/data_cleaned/demolition_sites.shp')
hubs.to_file('data/data_cleaned/hubs.shp')

<timed exec>:3: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.


CPU times: total: 5.7 s
Wall time: 5.88 s


In [176]:
%%time 
# read data 
edges = gpd.read_file('data/data_cleaned/ams_roads_edges.shp')
demSites = gpd.read_file('data/data_cleaned/demolition_sites.shp')
hubs = gpd.read_file('data/data_cleaned/hubs.shp')
conSites = gpd.read_file('data/data_cleaned/construction_sites.shp')
suppliers = gpd.read_file('data/data_cleaned/suppliers.shp')

# visualize data 
m = folium.Map([52.377231, 4.899288], zoom_start=11, tiles='cartodbdark_matter')
folium.GeoJson(water.to_crs('EPSG:4326').to_json()).add_to(m)
# folium.GeoJson(a10.to_json()).add_to(m)
# for _, row in edges.iterrows():
#     folium.PolyLine([(lat, lon) for lat, lon in zip(row.geometry.xy[1], row.geometry.xy[0])],
#                            color='grey', weight=1.5).add_to(m)
for _, row in hubs[hubs.waterbound == True].iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='blue', radius=0.5).add_to(m)
for _, row in hubs[hubs.waterbound == False].iterrows(): 
    folium.CircleMarker([row.geometry.y, row.geometry.x], 
                        color='red', radius=0.5).add_to(m)
# for _, row in hubs.iterrows(): 
#     folium.CircleMarker([row.geometry.y, row.geometry.x], 
#                         color='red', radius=3).add_to(m)
# for _, row in conSites.iterrows(): 
#     folium.CircleMarker([row.geometry.y, row.geometry.x], 
#                         color='green', radius=3).add_to(m)
# for _, row in suppliers.iterrows(): 
#     folium.CircleMarker([row.geometry.y, row.geometry.x], 
#                         color='lightblue', radius=0.5).add_to(m)

m

CPU times: total: 1.5 s
Wall time: 1.58 s
